## Data visualization

In [33]:
#import the nescessary libraries
import pandas as pd
import numpy as np

In [34]:

#Import the cleaned data set
df1 = pd.read_csv(r'..\output_data\transform_DF')
df1.tail()

Unnamed: 0  Bike_number           Start_Time             End_time  \
51388      154277        38999  2019-12-27 12:01:00  2019-12-27 12:13:00   
51389      154278        38999  2019-12-27 21:02:00  2019-12-27 21:16:00   
51390      154279        38999  2019-12-28 08:16:00  2019-12-28 08:27:00   
51391      154281        38999  2019-12-28 16:37:00  2019-12-28 16:53:00   
51392      154323        43400  2019-06-29 12:59:00  2019-06-29 13:14:00   

       Start_Longitude  Start_Latitude  End_Longitude  End_Latitude  \
51388         8.692439       50.128915       8.687546     50.115009   
51389         8.687546       50.115009       8.692439     50.128915   
51390         8.692439       50.128915       8.682500     50.115556   
51391         8.682500       50.115556       8.692439     50.128915   
51392         8.768889       50.134167       8.768889     50.134167   

       Start_Station  End_Station_number  Weekday  Duration  \
51388         4252.0              4247.0     True      12.0   
51389         4247.0              4252.0     True      14.0   
51390         4252.0             42006.0    False      11.0   
51391        42006.0              4252.0    False      16.0   
51392        42003.0             42003.0    False      15.0   

       Bikes_on_position  End_Bikes  Zip_codes  
51388                  1          8      60318  
51389                  8          1      60313  
51390                  1          3      60318  
51391                  3          1      60313  
51392                  4          3      60386

### Task 1: 
For the summer month (i.e., June, August, or September) with most trips, visualize the number of started trips per PLZ region (you’ll have to find geo data for that yourselves!) in a map.

The task requires geodata in order to visualize the number of trips by regions. The geodata available for this task is available on https://www.suche-postleitzahl.org/downloads.
The original file for administrative areas by postal code was available in .kml format. The file was then converted into geojson format for this project.

In [35]:
#Import the geojson data
import json
with open(r'..\data\ffpostcode.geojson') as json_data:
    ffgeo = json.load(json_data)
ffgeo

{'type': 'FeatureCollection',
 'name': 'PLZ 5-stellig Stadt Frankfurt am Main',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'Name': '60306',
    'description': '60306 Frankfurt am Main, Opernturm'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[8.6695498, 50.1158427],
      [8.6699022, 50.116553],
      [8.6706714, 50.1163693],
      [8.6705891, 50.1156601],
      [8.6707255, 50.1156328],
      [8.6707175, 50.1155649],
      [8.6695498, 50.1158427]]]}},
  {'type': 'Feature',
   'properties': {'Name': '60308', 'description': '60308 Frankfurt'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[8.6520947, 50.1121949],
      [8.6526051, 50.112719],
      [8.653367, 50.1124064],
      [8.6527681, 50.1118609],
      [8.6520947, 50.1121949]]]}},
  {'type': 'Feature',
   'properties': {'Name': '60310',
    'description': '60310 Frankfurt am Main (Taunusturm)'},
   'geometry': {'type'

The information we need is in the features keys. We can check the first data to see how it looks.
Also, the zipcode is in the key 'Name' in the 'properties' tab

In [36]:
ffgeo['features'][0]

{'type': 'Feature',
 'properties': {'Name': '60306',
  'description': '60306 Frankfurt am Main, Opernturm'},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[8.6695498, 50.1158427],
    [8.6699022, 50.116553],
    [8.6706714, 50.1163693],
    [8.6705891, 50.1156601],
    [8.6707255, 50.1156328],
    [8.6707175, 50.1155649],
    [8.6695498, 50.1158427]]]}}

In [37]:
#Create a new column called count in the base data frame. Assign each row value 1.
#Use the method groupby to group the data by zip_codes and calculate the sum of the count colum.
#Add the results to a new data frame with 2 columns 'Zipcodes' and 'Total trips'
df1['count'] = 1 
startbyzip = pd.DataFrame(df1[['Zip_codes', 'count']].groupby(['Zip_codes']).sum().reset_index().values.tolist(), columns = ['Zipcodes','Total_trips'])
startbyzip.tail()

Zipcodes  Total_trips
36     63067          467
37     65929          200
38     65933          127
39     65934           21
40     65936           10

This notebook uses the plotly library to visualize the cholorepth map

In [38]:
pip install plotly

In [39]:
#Use the plotly lib to visualize the map
#data for ploting is the startbyzip data frame, using the total trips for data and zipcodes for location
#featureidkey indicates the location of the region, the information is stored in the Name key of the properties tab
import plotly.express as px
fig = px.choropleth_mapbox(startbyzip, geojson=ffgeo, color='Total_trips',
                           locations='Zipcodes', featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

<center>Choropleth map of total trips by postal areas<center>

In [40]:
import datetime as dt
df1['Start_Time'] = pd.to_datetime(df1['Start_Time'], format="%Y-%m-%d %H:%M:%S")
df1['End_time'] = pd.to_datetime(df1['End_time'], format="%Y-%m-%d %H:%M:%S")
df1['Month'] = df1['Start_Time'].dt.month
df1.tail()

Unnamed: 0  Bike_number          Start_Time            End_time  \
51388      154277        38999 2019-12-27 12:01:00 2019-12-27 12:13:00   
51389      154278        38999 2019-12-27 21:02:00 2019-12-27 21:16:00   
51390      154279        38999 2019-12-28 08:16:00 2019-12-28 08:27:00   
51391      154281        38999 2019-12-28 16:37:00 2019-12-28 16:53:00   
51392      154323        43400 2019-06-29 12:59:00 2019-06-29 13:14:00   

       Start_Longitude  Start_Latitude  End_Longitude  End_Latitude  \
51388         8.692439       50.128915       8.687546     50.115009   
51389         8.687546       50.115009       8.692439     50.128915   
51390         8.692439       50.128915       8.682500     50.115556   
51391         8.682500       50.115556       8.692439     50.128915   
51392         8.768889       50.134167       8.768889     50.134167   

       Start_Station  End_Station_number  Weekday  Duration  \
51388         4252.0              4247.0     True      12.0   
51389         4247.0              4252.0     True      14.0   
51390         4252.0             42006.0    False      11.0   
51391        42006.0              4252.0    False      16.0   
51392        42003.0             42003.0    False      15.0   

       Bikes_on_position  End_Bikes  Zip_codes  count  Month  
51388                  1          8      60318      1     12  
51389                  8          1      60313      1     12  
51390                  1          3      60318      1     12  
51391                  3          1      60313      1     12  
51392                  4          3      60386      1      6

In [41]:
#Create the new data frame to start another task
df2 = df1.set_index('Start_Time')

In [42]:
#In order to explore the number of trips started by regions in the summer months, create dataframe for each months
df_jun = df2['2019-06-01 00:00:00':'2019-06-30 23:59:59']
df_aug = df2['2019-08-01 00:00:00':'2019-08-31 23:59:59']
df_sep = df2['2019-09-01 00:00:00':'2019-09-30 23:59:59']

In [43]:
#To further explore if summer months are different from winter, create a dataframe for December also
df_dec = df2['2019-12-01 00:00:00':'2019-12-31 23:59:59']

In [44]:
df_jun.tail()

Unnamed: 0  Bike_number            End_time  \
Start_Time                                                         
2019-06-16 16:19:00      154076        38999 2019-06-16 16:34:00   
2019-06-18 06:13:00      154081        38999 2019-06-18 06:28:00   
2019-06-18 13:42:00      154083        38999 2019-06-18 14:03:00   
2019-06-18 14:50:00      154084        38999 2019-06-18 15:45:00   
2019-06-29 12:59:00      154323        43400 2019-06-29 13:14:00   

                     Start_Longitude  Start_Latitude  End_Longitude  \
Start_Time                                                            
2019-06-16 16:19:00         8.698785       50.115535       8.701086   
2019-06-18 06:13:00         8.681801       50.109113       8.709562   
2019-06-18 13:42:00         8.709562       50.111452       8.685041   
2019-06-18 14:50:00         8.685041       50.099555       8.685041   
2019-06-29 12:59:00         8.768889       50.134167       8.768889   

                     End_Latitude  Start_Station  End_Station_number  Weekday  \
Start_Time                                                                      
2019-06-16 16:19:00     50.110389         4248.0              4285.0    False   
2019-06-18 06:13:00     50.111452         4192.0              4296.0     True   
2019-06-18 13:42:00     50.099555         4296.0              4260.0     True   
2019-06-18 14:50:00     50.099555         4260.0              4260.0     True   
2019-06-29 12:59:00     50.134167        42003.0             42003.0    False   

                     Duration  Bikes_on_position  End_Bikes  Zip_codes  count  \
Start_Time                                                                      
2019-06-16 16:19:00      15.0                  1          5      60316      1   
2019-06-18 06:13:00      15.0                  1          1      60311      1   
2019-06-18 13:42:00      21.0                  1          5      60314      1   
2019-06-18 14:50:00      55.0                  5          5      60594      1   
2019-06-29 12:59:00      15.0                  4          3      60386      1   

                     Month  
Start_Time                  
2019-06-16 16:19:00      6  
2019-06-18 06:13:00      6  
2019-06-18 13:42:00      6  
2019-06-18 14:50:00      6  
2019-06-29 12:59:00      6

In [45]:
#As we need to visualize the number of trips, perform the groupby method and sum the count column to get the number of trips by postcode
startbyzip_jun = pd.DataFrame(df_jun[['Zip_codes', 'count']].groupby(['Zip_codes']).sum().reset_index().values.tolist(), columns = ['Zipcodes','Total_trips'])
startbyzip_aug = pd.DataFrame(df_aug[['Zip_codes', 'count']].groupby(['Zip_codes']).sum().reset_index().values.tolist(), columns = ['Zipcodes','Total_trips'])
startbyzip_sep = pd.DataFrame(df_sep[['Zip_codes', 'count']].groupby(['Zip_codes']).sum().reset_index().values.tolist(), columns = ['Zipcodes','Total_trips'])
startbyzip_dec = pd.DataFrame(df_dec[['Zip_codes', 'count']].groupby(['Zip_codes']).sum().reset_index().values.tolist(), columns = ['Zipcodes','Total_trips'])

In [46]:
#Use the plotly lib to visualize the map
#data for ploting is the startbyzip data frame, using the total trips for data and zipcodes for location
#featureidkey indicates the location of the region, the information is stored in the Name key of the properties
fig = px.choropleth_mapbox(startbyzip_jun, 
                           geojson=ffgeo, 
                           color='Total_trips',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of started trips by Postal Region in Jun, 2019<center>

In [47]:
fig = px.choropleth_mapbox(startbyzip_aug, 
                           geojson=ffgeo, 
                           color='Total_trips',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of started trips by Postal Region in Aug, 2019<center>

In [48]:
fig = px.choropleth_mapbox(startbyzip_sep, 
                           geojson=ffgeo, 
                           color='Total_trips',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of started trips by Postal Region in Sep, 2019<center>

In [49]:
fig = px.choropleth_mapbox(startbyzip_dec, 
                           geojson=ffgeo, 
                           color='Total_trips',
                           locations='Zipcodes', featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of started trips by Postal Region in Dec, 2019<center>

The maps show a consistent pattern that more trips are generated within the city center than the surrounding areas. In other words, the closer the region is to the city center, the more trips are generated in that region. This pattern holds true for the summer months, which are June, August, and September. To discover if this pattern exists in the winter, we also visualized the total trips by the starting PLZ region in the month December. The result shows a similar trend that the further the regions are from the center, the less trip generated.

We further explore the duration of trips by their starting locations. The purpose is to check if there is a difference in duration for trips that started from different regions.

In [50]:
#Perform the similar method as done for number of trips, but change the Total Trips by Duration
#And use the mean() method instead of the sum.
startbyzip_jun = pd.DataFrame(df_jun[['Zip_codes', 'Duration']].groupby(['Zip_codes']).mean().reset_index().values.tolist(), columns = ['Zipcodes','AVG_duration'])
startbyzip_aug = pd.DataFrame(df_aug[['Zip_codes', 'Duration']].groupby(['Zip_codes']).mean().reset_index().values.tolist(), columns = ['Zipcodes','AVG_duration'])
startbyzip_sep = pd.DataFrame(df_sep[['Zip_codes', 'Duration']].groupby(['Zip_codes']).mean().reset_index().values.tolist(), columns = ['Zipcodes','AVG_duration'])
startbyzip_dec = pd.DataFrame(df_dec[['Zip_codes', 'Duration']].groupby(['Zip_codes']).mean().reset_index().values.tolist(), columns = ['Zipcodes','AVG_duration'])

In [51]:
fig = px.choropleth_mapbox(startbyzip_jun, 
                           geojson=ffgeo, 
                           color='AVG_duration',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of duration of the trips by their starting postal Region in Jun, 2019<center>

In [52]:
fig = px.choropleth_mapbox(startbyzip_aug, 
                           geojson=ffgeo, 
                           color='AVG_duration',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of duration of the trips by their starting postal Region in Aug, 2019<center>

In [53]:
fig = px.choropleth_mapbox(startbyzip_sep, 
                           geojson=ffgeo, 
                           color='AVG_duration',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of duration of the trips by their starting postal Region in Sep, 2019<center>

In [54]:
fig = px.choropleth_mapbox(startbyzip_dec, 
                           geojson=ffgeo, 
                           color='AVG_duration',
                           locations='Zipcodes', 
                           featureidkey='properties.Name',
                           center={'lat': 50.107254, 'lon': 8.685223},
                           mapbox_style="carto-positron", 
                           zoom=10)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

#### <center>Figure: Map of duration of the trips by their starting postal Region in Dec, 2019<center>

As we explored further, we also plotted the average duration of the trips by the region they started on the map by PLZ regions. Figure X, X, and X display the average duration of the trips by the starting PLZ regions. One consistent pattern was identified. The average duration of trips that started in the center regions were  shorter than that of trips started in the border regions. This pattern holds true for both summer months and December, 2019. Based on this finding, we hypothesized that the region from which the trips started could be a predictor for trip duration. Therefore, we included the Border_district (binary) as a predictor for our prediction model, which will be reported later in this report.

### Task 3: 
Create a heatmap based on an interesting aspect of the data, e.g., end locations of trips shortly before the start of a major public event.

A fraction of the visualization task was to investigate the interesting aspect of the data. As such, we employed the heatmap to discover two parts of the biker using behavior:

<b>Explore whether people would use bikes to travel to public events </b>

In order to investigate this, two public events were selected. The first one was the IAA 2019 event, one of the leading mobility exhibitions worldwide. The second event was a football match between Frankfurt home team, Eintracht Frankfurt, and Dortmund. There are two reasons for the selection of the two mentioned events. Firstly, the locations of the two events have different distances to the city center. While Messe Frankfurt exhibition center is located near the city center area, Commerzbank-Arena is more in the outskirts. Therefore, there might be different patterns in bike usage caused by the location of the event. Secondly, the IAA event was open for visit for a period of 10 days, whereas the football match was a one-time event. As such, this could be a factor that affects user behavior. The followings are the details of the two events and the results of the visualization:


<b>IAA 2019</b> \
Location: Messe Frankfurt exhibition center\
Visit day: From 12 to 22 September, 2019\
Visit hours: Daily from 09:00 am to 07:00 pm, 20th of September from 11 am to 9 pm.


In [55]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library


print('Folium installed')
print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Folium installed
Libraries imported.


In [56]:
#Use Nominatim to get the location information of the event
address = 'Messe Frankfurt'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('Location of the ', address, latitude, longitude)

Location of the  Messe Frankfurt 50.1115525 8.64793168801447


In [57]:
#As the event was open for a period of time, we will use the heatmap with timestamp to see the end trips by day
from folium.plugins import HeatMapWithTime

In [58]:
#To make it easier to select the day and time later, create new columns for the week, day, and hour
df1['week'] = df1['End_time'].dt.week
df1['day'] = df1['End_time'].dt.day
df1['hour'] = df1['End_time'].dt.hour
df1.tail()

Unnamed: 0  Bike_number          Start_Time            End_time  \
51388      154277        38999 2019-12-27 12:01:00 2019-12-27 12:13:00   
51389      154278        38999 2019-12-27 21:02:00 2019-12-27 21:16:00   
51390      154279        38999 2019-12-28 08:16:00 2019-12-28 08:27:00   
51391      154281        38999 2019-12-28 16:37:00 2019-12-28 16:53:00   
51392      154323        43400 2019-06-29 12:59:00 2019-06-29 13:14:00   

       Start_Longitude  Start_Latitude  End_Longitude  End_Latitude  \
51388         8.692439       50.128915       8.687546     50.115009   
51389         8.687546       50.115009       8.692439     50.128915   
51390         8.692439       50.128915       8.682500     50.115556   
51391         8.682500       50.115556       8.692439     50.128915   
51392         8.768889       50.134167       8.768889     50.134167   

       Start_Station  End_Station_number  Weekday  Duration  \
51388         4252.0              4247.0     True      12.0   
51389         4247.0              4252.0     True      14.0   
51390         4252.0             42006.0    False      11.0   
51391        42006.0              4252.0    False      16.0   
51392        42003.0             42003.0    False      15.0   

       Bikes_on_position  End_Bikes  Zip_codes  count  Month  week  day  hour  
51388                  1          8      60318      1     12    52   27    12  
51389                  8          1      60313      1     12    52   27    21  
51390                  1          3      60318      1     12    52   28     8  
51391                  3          1      60313      1     12    52   28    16  
51392                  4          3      60386      1      6    26   29    13

In [59]:
#To start the new task, create a new dataframe with index = 'end_time' for easy select
df10 = df1.set_index('End_time')
df10.tail()

Unnamed: 0  Bike_number          Start_Time  \
End_time                                                           
2019-12-27 12:13:00      154277        38999 2019-12-27 12:01:00   
2019-12-27 21:16:00      154278        38999 2019-12-27 21:02:00   
2019-12-28 08:27:00      154279        38999 2019-12-28 08:16:00   
2019-12-28 16:53:00      154281        38999 2019-12-28 16:37:00   
2019-06-29 13:14:00      154323        43400 2019-06-29 12:59:00   

                     Start_Longitude  Start_Latitude  End_Longitude  \
End_time                                                              
2019-12-27 12:13:00         8.692439       50.128915       8.687546   
2019-12-27 21:16:00         8.687546       50.115009       8.692439   
2019-12-28 08:27:00         8.692439       50.128915       8.682500   
2019-12-28 16:53:00         8.682500       50.115556       8.692439   
2019-06-29 13:14:00         8.768889       50.134167       8.768889   

                     End_Latitude  Start_Station  End_Station_number  Weekday  \
End_time                                                                        
2019-12-27 12:13:00     50.115009         4252.0              4247.0     True   
2019-12-27 21:16:00     50.128915         4247.0              4252.0     True   
2019-12-28 08:27:00     50.115556         4252.0             42006.0    False   
2019-12-28 16:53:00     50.128915        42006.0              4252.0    False   
2019-06-29 13:14:00     50.134167        42003.0             42003.0    False   

                     Duration  Bikes_on_position  End_Bikes  Zip_codes  count  \
End_time                                                                        
2019-12-27 12:13:00      12.0                  1          8      60318      1   
2019-12-27 21:16:00      14.0                  8          1      60313      1   
2019-12-28 08:27:00      11.0                  1          3      60318      1   
2019-12-28 16:53:00      16.0                  3          1      60313      1   
2019-06-29 13:14:00      15.0                  4          3      60386      1   

                     Month  week  day  hour  
End_time                                     
2019-12-27 12:13:00     12    52   27    12  
2019-12-27 21:16:00     12    52   27    21  
2019-12-28 08:27:00     12    52   28     8  
2019-12-28 16:53:00     12    52   28    16  
2019-06-29 13:14:00      6    26   29    13

In [60]:
#Select only data for the 5days before the event and during the event to see the difference
df10 = df10['2019-09-07 00:00:00':'2019-09-22 23:59:59']
df10['day'].value_counts()

14    371
13    318
20    303
21    288
16    285
17    281
18    270
19    266
12    262
15    259
11    256
10    251
22    219
9     214
7     127
8      90
Name: day, dtype: int64

In [61]:
#as the event was open from 9AM to 7AM, filter only trips that ended from 1 hour before the start time
#and not after the finish time
df11 = df10[df10['hour']>8]
df12 = df11[df11['hour']<19]
df12.head()

Unnamed: 0  Bike_number          Start_Time  \
End_time                                                           
2019-09-08 13:11:00         304        38001 2019-09-08 12:54:00   
2019-09-09 12:59:00         307        38001 2019-09-09 12:44:00   
2019-09-09 15:33:00         308        38001 2019-09-09 15:21:00   
2019-09-09 18:20:00         309        38001 2019-09-09 18:08:00   
2019-09-10 13:41:00         311        38001 2019-09-10 13:16:00   

                     Start_Longitude  Start_Latitude  End_Longitude  \
End_time                                                              
2019-09-08 13:11:00         8.643708       50.104957       8.671153   
2019-09-09 12:59:00         8.643708       50.104957       8.678609   
2019-09-09 15:33:00         8.678609       50.113124       8.655647   
2019-09-09 18:20:00         8.655647       50.109791       8.636048   
2019-09-10 13:41:00         8.636048       50.102132       8.678609   

                     End_Latitude  Start_Station  End_Station_number  Weekday  \
End_time                                                                        
2019-09-08 13:11:00     50.115329         4195.0              4243.0    False   
2019-09-09 12:59:00     50.113124         4195.0              4245.0     True   
2019-09-09 15:33:00     50.109791         4245.0                 0.0     True   
2019-09-09 18:20:00     50.102132            0.0              4205.0     True   
2019-09-10 13:41:00     50.113124         4205.0              4245.0     True   

                     Duration  Bikes_on_position  End_Bikes  Zip_codes  count  \
End_time                                                                        
2019-09-08 13:11:00      17.0                  6          3      60327      1   
2019-09-09 12:59:00      15.0                  2          3      60327      1   
2019-09-09 15:33:00      12.0                  3          1      60313      1   
2019-09-09 18:20:00      12.0                  1          6      60327      1   
2019-09-10 13:41:00      25.0                  7          7      60326      1   

                     Month  week  day  hour  
End_time                                     
2019-09-08 13:11:00      9    36    8    13  
2019-09-09 12:59:00      9    37    9    12  
2019-09-09 15:33:00      9    37    9    15  
2019-09-09 18:20:00      9    37    9    18  
2019-09-10 13:41:00      9    37   10    13

In [62]:
#To create the heat map with time, we have to create the data, which is the format [[lat, lon], weight]
#To do this, we first create an empty list to store the data
#Then, use the for loop to get the day from the dataframe and use the day to access the data, then group them by location, and sum the counts for total trips
df_time = []
for day in df12.day.sort_values().unique():
    df_time.append(df12.loc[df12.day == day, ['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist())

In [63]:
#Create an empty map and add the marker to mark the location of the event location
ffmap1 = folium.Map(location=[50.107254, 8.685223], zoom_start=12)
folium.Marker(
    [latitude, longitude],
    popup=address
).add_to(ffmap1)

In [65]:
#create the HeatMapWithTime plugin and add it to the map
hm = HeatMapWithTime(df_time, radius=13, min_opacity=0.5, max_opacity=0.8,gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, use_local_extrema=True, auto_play = True)
hm.add_to(ffmap1)
ffmap1

A heatmap with time slider was utilized to investigate if Frankfurt citizens used bikes to commute to the IAA event during its opening hours. Since the event was open 11 days and the opening hours ranged from morning to evening, visitors could decide their time for the visit. As such, we employed the data of the trips that ended 1 hour before the opening time and before the event daily end time for the visualization. The heatmap ran through 5 days before the event started and during the visiting days. The map visualization shows that there were trips that ended next to the exhibition center during the opening hours. Also, Weekends captured more trips to the event location than that of normal. In addition, as the event came closer to its end, more trips that ended near the exhibition center were captured in the map. Interestingly, 2 days before the first opening day, there were trips that ended inside the exhibition center. This could be explained that event staff and volunteers might have organized their preparation meeting before the event started.

<b>Football match between Eintracht Frankfurt and Dortmund</b> \
Location: Commerzbank-Arena, Frankfurt\
Date and time: 18:00 CEST on 22 September, 2019\
Attendance: 51,500\


In [66]:
#Use Nominatim to get the location information of the event
address = 'Commerzbank-Arena'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('Location of the ', address, latitude, longitude)

Location of the  Commerzbank-Arena 50.06857865 8.645519952099118


In [67]:
#To start the new task, create a new dataframe with index = 'end_time' for easy select
df11 = df1.set_index('End_time')
df11.tail()

Unnamed: 0  Bike_number          Start_Time  \
End_time                                                           
2019-12-27 12:13:00      154277        38999 2019-12-27 12:01:00   
2019-12-27 21:16:00      154278        38999 2019-12-27 21:02:00   
2019-12-28 08:27:00      154279        38999 2019-12-28 08:16:00   
2019-12-28 16:53:00      154281        38999 2019-12-28 16:37:00   
2019-06-29 13:14:00      154323        43400 2019-06-29 12:59:00   

                     Start_Longitude  Start_Latitude  End_Longitude  \
End_time                                                              
2019-12-27 12:13:00         8.692439       50.128915       8.687546   
2019-12-27 21:16:00         8.687546       50.115009       8.692439   
2019-12-28 08:27:00         8.692439       50.128915       8.682500   
2019-12-28 16:53:00         8.682500       50.115556       8.692439   
2019-06-29 13:14:00         8.768889       50.134167       8.768889   

                     End_Latitude  Start_Station  End_Station_number  Weekday  \
End_time                                                                        
2019-12-27 12:13:00     50.115009         4252.0              4247.0     True   
2019-12-27 21:16:00     50.128915         4247.0              4252.0     True   
2019-12-28 08:27:00     50.115556         4252.0             42006.0    False   
2019-12-28 16:53:00     50.128915        42006.0              4252.0    False   
2019-06-29 13:14:00     50.134167        42003.0             42003.0    False   

                     Duration  Bikes_on_position  End_Bikes  Zip_codes  count  \
End_time                                                                        
2019-12-27 12:13:00      12.0                  1          8      60318      1   
2019-12-27 21:16:00      14.0                  8          1      60313      1   
2019-12-28 08:27:00      11.0                  1          3      60318      1   
2019-12-28 16:53:00      16.0                  3          1      60313      1   
2019-06-29 13:14:00      15.0                  4          3      60386      1   

                     Month  week  day  hour  
End_time                                     
2019-12-27 12:13:00     12    52   27    12  
2019-12-27 21:16:00     12    52   27    21  
2019-12-28 08:27:00     12    52   28     8  
2019-12-28 16:53:00     12    52   28    16  
2019-06-29 13:14:00      6    26   29    13

In [68]:
#Select only data for the 5days before the event and during the event to see the difference
df11 = df11['2019-09-22 16:30:00':'2019-09-22 18:00:00']

In [69]:
#Create an empty map and add the marker to mark the location of the event location
ffmap2 = folium.Map(location=[50.107254, 8.685223], zoom_start=12)
folium.Marker(
    [latitude, longitude],
    popup=address
).add_to(ffmap2)
from folium.plugins import HeatMap
HeatMap(data=df11[['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist(),
        radius=8, 
        max_zoom=13).add_to(ffmap2)
ffmap2

To investigate if people commuted to the football match using bikes, data for the trips that ended 1.5 hour before the match started was employed in the visualization. In contrast to the IAA event, the map shows nearly no bike trips ended near the Commerzbank-Arena before the match started. The location of the Commerzbank-Arena might be a decisive factor in this case. The stadium was far from the city center. Also, the bike route to commute from the city center to the stadium might be difficult.

### Task 2:
For one moment in time, visualize the number of bikes at fixed stations meaningfully.

<b>Explore whether students would use bikes to travel to university.</b> \
In Germany, the normal lecture time in University is from 8AM. Therefore, we employed the data of trips ending from 7AM to 8AM to investigate if there were bikes that ended near the university campus before the lectures started. We first visualized the number of bikes at fixed stations from 7AM to 8AM on two days May 03 and May 08 2019 (normal weekdays) to check our assumption that students would use bikes to commute from home to school. 

In [70]:
#credit to Marcel Motta, https://stackoverflow.com/questions/55571311/get-part-of-day-morning-afternoon-evening-night-in-python-dataframe
df1['period_of_day'] = (df1['Start_Time'].dt.hour % 24 + 4) // 4
df1['period_of_day'].replace({1: 'Late Night',
                      2: 'Early Morning',
                      3: 'Morning',
                      4: 'Noon',
                      5: 'Evening',
                      6: 'Night'}, inplace=True)

In [71]:
df1.tail()

Unnamed: 0  Bike_number          Start_Time            End_time  \
51388      154277        38999 2019-12-27 12:01:00 2019-12-27 12:13:00   
51389      154278        38999 2019-12-27 21:02:00 2019-12-27 21:16:00   
51390      154279        38999 2019-12-28 08:16:00 2019-12-28 08:27:00   
51391      154281        38999 2019-12-28 16:37:00 2019-12-28 16:53:00   
51392      154323        43400 2019-06-29 12:59:00 2019-06-29 13:14:00   

       Start_Longitude  Start_Latitude  End_Longitude  End_Latitude  \
51388         8.692439       50.128915       8.687546     50.115009   
51389         8.687546       50.115009       8.692439     50.128915   
51390         8.692439       50.128915       8.682500     50.115556   
51391         8.682500       50.115556       8.692439     50.128915   
51392         8.768889       50.134167       8.768889     50.134167   

       Start_Station  End_Station_number  ...  Duration  Bikes_on_position  \
51388         4252.0              4247.0  ...      12.0                  1   
51389         4247.0              4252.0  ...      14.0                  8   
51390         4252.0             42006.0  ...      11.0                  1   
51391        42006.0              4252.0  ...      16.0                  3   
51392        42003.0             42003.0  ...      15.0                  4   

       End_Bikes  Zip_codes  count  Month  week  day  hour  period_of_day  
51388          8      60318      1     12    52   27    12           Noon  
51389          1      60313      1     12    52   27    21          Night  
51390          3      60318      1     12    52   28     8        Morning  
51391          1      60313      1     12    52   28    16        Evening  
51392          3      60386      1      6    26   29    13           Noon  

[5 rows x 21 columns]

In [72]:
# create a new map  around city in study with a high zoom level
ffmap7 = folium.Map(location=[50.107254, 8.685223], zoom_start=10)

# display world map
ffmap7

In [73]:
address = 'Frankfurt University of Applied Sciences'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('Location of the ', address, latitude, longitude)

Location of the  Frankfurt University of Applied Sciences 50.130519449999994 8.692339207868319


In [74]:
#create a new dataframe to start new task
df4 = df1.set_index('period_of_day')

In [75]:
df4.head()

Unnamed: 0  Bike_number          Start_Time  \
period_of_day                                                
Noon                   13        11451 2019-05-30 15:42:00   
Late Night             14        11451 2019-05-31 02:22:00   
Early Morning          22        11542 2019-09-10 06:53:00   
Evening                26        11542 2019-09-10 19:57:00   
Early Morning          28        11542 2019-09-11 06:48:00   

                         End_time  Start_Longitude  Start_Latitude  \
period_of_day                                                        
Noon          2019-05-30 17:22:00         8.553437       50.101748   
Late Night    2019-05-31 02:32:00         8.554450       50.101711   
Early Morning 2019-09-10 07:28:00         8.664168       50.107599   
Evening       2019-09-10 20:06:00         8.664168       50.107599   
Early Morning 2019-09-11 06:55:00         8.664168       50.107599   

               End_Longitude  End_Latitude  Start_Station  End_Station_number  \
period_of_day                                                                   
Noon                8.554450     50.101711         4291.0                 0.0   
Late Night          8.556589     50.114979            0.0                 0.0   
Early Morning       8.611191     50.124972         4240.0                 0.0   
Evening             8.664168     50.107599         4240.0              4240.0   
Early Morning       8.664168     50.107599         4240.0              4240.0   

               Weekday  Duration  Bikes_on_position  End_Bikes  Zip_codes  \
period_of_day                                                               
Noon              True     100.0                  5          1      65929   
Late Night        True      10.0                  1          1      65929   
Early Morning     True      35.0                  9          1      60329   
Evening           True       9.0                  6          5      60329   
Early Morning     True       7.0                  1          1      60329   

               count  Month  week  day  hour  
period_of_day                                 
Noon               1      5    22   30    17  
Late Night         1      5    22   31     2  
Early Morning      1      9    37   10     7  
Evening            1      9    37   10    20  
Early Morning      1      9    37   11     6

In [76]:
#Select May as the first month to start, and store in a new datadrame
df_5 = df4[df4['Month']==5]
df_5.reset_index(inplace= True)
df_5.set_index('End_time', inplace = True)

In [77]:
#select the period from 7AM to 8AM
#and then select the date May 3rd
df_5_8 = df_5[df_5['hour'] == 7]
df_5_8 = df_5_8[df_5_8['day'] == 3]
df_5_8.head()

period_of_day  Unnamed: 0  Bike_number  \
End_time                                                      
2019-05-03 07:00:00  Early Morning        2760        38011   
2019-05-03 07:00:00  Early Morning       27185        38131   
2019-05-03 07:38:00  Early Morning       40174        38199   
2019-05-03 07:28:00  Early Morning       56535        38291   
2019-05-03 07:40:00  Early Morning       86214        38468   

                             Start_Time  Start_Longitude  Start_Latitude  \
End_time                                                                   
2019-05-03 07:00:00 2019-05-03 06:44:00         8.628361       50.101643   
2019-05-03 07:00:00 2019-05-03 06:50:00         8.643708       50.104957   
2019-05-03 07:38:00 2019-05-03 07:28:00         8.649270       50.116870   
2019-05-03 07:28:00 2019-05-03 07:09:00         8.671153       50.115329   
2019-05-03 07:40:00 2019-05-03 07:26:00         8.681114       50.101915   

                     End_Longitude  End_Latitude  Start_Station  \
End_time                                                          
2019-05-03 07:00:00       8.663417     50.101364         4204.0   
2019-05-03 07:00:00       8.654920     50.108824         4195.0   
2019-05-03 07:38:00       8.658460     50.123192         4181.0   
2019-05-03 07:28:00       8.709562     50.111452         4243.0   
2019-05-03 07:40:00       8.703323     50.107547         4261.0   

                     End_Station_number  Weekday  Duration  Bikes_on_position  \
End_time                                                                        
2019-05-03 07:00:00              4304.0     True      16.0                  3   
2019-05-03 07:00:00              4295.0     True      10.0                  5   
2019-05-03 07:38:00              4221.0     True      10.0                  1   
2019-05-03 07:28:00              4296.0     True      19.0                  5   
2019-05-03 07:40:00              4216.0     True      14.0                  5   

                     End_Bikes  Zip_codes  count  Month  week  day  hour  
End_time                                                                  
2019-05-03 07:00:00          2      60326      1      5    18    3     7  
2019-05-03 07:00:00          3      60327      1      5    18    3     7  
2019-05-03 07:38:00          5      60325      1      5    18    3     7  
2019-05-03 07:28:00          2      60322      1      5    18    3     7  
2019-05-03 07:40:00          2      60594      1      5    18    3     7

In [78]:
df_5_8.reset_index(inplace = True)

In [79]:
# create a new map  around city in study with a high zoom level
ffmap7 = folium.Map(location=[50.107254, 8.685223], zoom_start=12)
folium.Marker([50.130519449999994,8.692339207868319], popup=address).add_to(ffmap7)

#Use the for loop to plot cirle markers on the map. 
#The cirle markers have radiuses vary depending on the number of bikes at stations when the trip ended
#The fill opacity of the cirle also varys depending on the number of bikes at stations when the trip ended

for i in range(0,len(df_5_8)):
    lat = df_5_8.iloc[i]['End_Latitude']
    lon = df_5_8.iloc[i]['End_Longitude']
    radius = int(df_5_8.iloc[i]['End_Bikes']*5)
    folium.CircleMarker(
        location =[lat, lon],
        radius = radius,
        color = 'teal',
        fill_color = 'teal',
        fill_opacity = 0.2*df_5_8.iloc[i]['End_Bikes']).add_to(ffmap7)
ffmap7

In [80]:
#select the period from 7AM to 8AM
#and then select the date May 8th
df_5_8 = df_5[df_5['hour'] == 7]
df_5_8 = df_5_8[df_5_8['day'] == 8]
df_5_8.reset_index(inplace = True)

In [81]:
# create a new map  around city in study with a high zoom level
ffmap7 = folium.Map(location=[50.107254, 8.685223], zoom_start=12)
folium.Marker([50.130519449999994,8.692339207868319], popup=address).add_to(ffmap7)

#Use the for loop to plot cirle markers on the map. 
#The cirle markers have radiuses vary depending on the number of bikes at stations when the trip ended
#The fill opacity of the cirle also varys depending on the number of bikes at stations when the trip ended

for i in range(0,len(df_5_8)):
    lat = df_5_8.iloc[i]['End_Latitude']
    lon = df_5_8.iloc[i]['End_Longitude']
    radius = int(df_5_8.iloc[i]['End_Bikes']*5)
    folium.CircleMarker(
        location =[lat, lon],
        radius = radius,
        color = 'teal',
        fill_color = 'teal',
        fill_opacity = 0.2*df_5_8.iloc[i]['End_Bikes']).add_to(ffmap7)
ffmap7

Using a Folium map with circle markers, whose size represents the number of bikes at the station when the trips ended, we captured the result that was inline with our expectation. From 7AM to 8AM on the selected days, the stations near the University of Applied Sciences were among the top stations with more bikes.

To further discover this bike using pattern, we utilized the heatmap with time to visualize the end locations of the trips that ended from 7AM to 8AM everyday in May, August, September, October. 

In [82]:
#select the time period from 7Am to 8AM for May
df_5_9 = df_5[df_5['hour'] == 7]
df_5_9.tail()

period_of_day  Unnamed: 0  Bike_number  \
End_time                                                      
2019-05-15 07:03:00  Early Morning      150614        38983   
2019-05-20 07:21:00  Early Morning      150630        38983   
2019-05-27 07:26:00  Early Morning      150642        38983   
2019-05-02 07:12:00  Early Morning      151771        38988   
2019-05-28 07:42:00  Early Morning      152261        38990   

                             Start_Time  Start_Longitude  Start_Latitude  \
End_time                                                                   
2019-05-15 07:03:00 2019-05-15 06:51:00         8.671582       50.131360   
2019-05-20 07:21:00 2019-05-20 06:57:00         8.664168       50.107599   
2019-05-27 07:26:00 2019-05-27 07:14:00         8.640082       50.119147   
2019-05-02 07:12:00 2019-05-02 06:57:00         8.649958       50.114352   
2019-05-28 07:42:00 2019-05-28 07:34:00         8.692180       50.130390   

                     End_Longitude  End_Latitude  Start_Station  \
End_time                                                          
2019-05-15 07:03:00       8.671153     50.115329         4223.0   
2019-05-20 07:21:00       8.664168     50.107599         4240.0   
2019-05-27 07:26:00       8.640082     50.119147         4200.0   
2019-05-02 07:12:00       8.679596     50.125765         4279.0   
2019-05-28 07:42:00       8.692680     50.123068         4227.0   

                     End_Station_number  Weekday  Duration  Bikes_on_position  \
End_time                                                                        
2019-05-15 07:03:00              4243.0     True      12.0                  5   
2019-05-20 07:21:00              4240.0     True      24.0                  5   
2019-05-27 07:26:00              4200.0     True      12.0                  5   
2019-05-02 07:12:00              4131.0     True      15.0                  2   
2019-05-28 07:42:00              4250.0     True       8.0                  1   

                     End_Bikes  Zip_codes  count  Month  week  day  hour  
End_time                                                                  
2019-05-15 07:03:00          4      60323      1      5    20   15     7  
2019-05-20 07:21:00          5      60329      1      5    21   20     7  
2019-05-27 07:26:00          5      60486      1      5    22   27     7  
2019-05-02 07:12:00          3      60486      1      5    18    2     7  
2019-05-28 07:42:00          4      60318      1      5    22   28     7

In [83]:
#create a blank map using folium, and add a location marker of the university
ffmap11 = folium.Map(location=[50.107254, 8.685223], zoom_start=10)
folium.Marker(
    [50.130519449999994,8.692339207868319],
    popup=address,
).add_to(ffmap11)

#Using the same method to create heatmap with time
#Create an empty list to store the data
#Then, use the for loop to get the day from the dataframe and use the day to access the data, 
#Then group them by location, and sum the counts for total trips

df_time = []
for day in df_5_9.day.sort_values().unique():
    df_time.append(df_5_9.loc[df_5_9.day == day, ['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist())
    
hm = HeatMapWithTime(df_time, radius=13, min_opacity=0.5, max_opacity=0.8,gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, use_local_extrema=True, auto_play = True)
hm.add_to(ffmap11)
ffmap11

TypeError: __init__() got an unexpected keyword argument 'gradient'

In [84]:
#Select the month August
#select the time period from 7Am to 8AM for August
#Store in new dataframe
df_8 = df4[df4['Month']==8]
df_8.reset_index(inplace= True)
df_8.set_index('End_time', inplace = True)
df_8 = df_8[df_8['hour'] == 7]
df_8.tail()

period_of_day  Unnamed: 0  Bike_number  \
End_time                                                      
2019-08-14 07:28:00  Early Morning      153212        38995   
2019-08-23 07:48:00  Early Morning      153553        38996   
2019-08-09 07:57:00  Early Morning      154112        38999   
2019-08-13 07:20:00  Early Morning      154114        38999   
2019-08-30 07:07:00  Early Morning      154138        38999   

                             Start_Time  Start_Longitude  Start_Latitude  \
End_time                                                                   
2019-08-14 07:28:00 2019-08-14 07:19:00         8.645661       50.131105   
2019-08-23 07:48:00 2019-08-23 06:14:00         8.632768       50.115334   
2019-08-09 07:57:00 2019-08-09 07:25:00         8.664663       50.105688   
2019-08-13 07:20:00 2019-08-13 06:50:00         8.636048       50.102132   
2019-08-30 07:07:00 2019-08-30 05:41:00         8.684762       50.096708   

                     End_Longitude  End_Latitude  Start_Station  \
End_time                                                          
2019-08-14 07:28:00       8.640082     50.119147         4203.0   
2019-08-23 07:48:00       8.692180     50.130390            0.0   
2019-08-09 07:57:00       8.669271     50.139557            0.0   
2019-08-13 07:20:00       8.685041     50.099555         4205.0   
2019-08-30 07:07:00       8.692439     50.128915            0.0   

                     End_Station_number  Weekday  Duration  Bikes_on_position  \
End_time                                                                        
2019-08-14 07:28:00              4200.0     True       9.0                  2   
2019-08-23 07:48:00              4227.0     True      94.0                  1   
2019-08-09 07:57:00                 0.0     True      32.0                  1   
2019-08-13 07:20:00              4260.0     True      30.0                  1   
2019-08-30 07:07:00              4252.0     True      86.0                  1   

                     End_Bikes  Zip_codes  count  Month  week  day  hour  
End_time                                                                  
2019-08-14 07:28:00          7      60487      1      8    33   14     7  
2019-08-23 07:48:00         10      60486      1      8    34   23     7  
2019-08-09 07:57:00          1      60329      1      8    32    9     7  
2019-08-13 07:20:00          5      60326      1      8    33   13     7  
2019-08-30 07:07:00         10      60598      1      8    35   30     7

In [85]:
df_5_8 = df_5[df_5['hour'] == 10]
df_5_8 = df_5_8[df_5_8['day'] == 3]
df_5_8.head()

period_of_day  Unnamed: 0  Bike_number  \
End_time                                                     
2019-05-03 10:23:00       Morning       10161        38040   
2019-05-03 10:14:00       Morning       25994        38128   
2019-05-03 10:24:00       Morning       50203        38258   
2019-05-03 10:20:00       Morning       66613        38344   
2019-05-03 10:37:00       Morning       73700        38407   

                             Start_Time  Start_Longitude  Start_Latitude  \
End_time                                                                   
2019-05-03 10:23:00 2019-05-03 09:54:00         8.658460       50.123192   
2019-05-03 10:14:00 2019-05-03 09:53:00         8.678609       50.113124   
2019-05-03 10:24:00 2019-05-03 09:52:00         8.658460       50.123192   
2019-05-03 10:20:00 2019-05-03 09:52:00         8.658460       50.123192   
2019-05-03 10:37:00 2019-05-03 10:13:00         8.678609       50.113124   

                     End_Longitude  End_Latitude  Start_Station  \
End_time                                                          
2019-05-03 10:23:00       8.658460     50.123192         4221.0   
2019-05-03 10:14:00       8.678609     50.113124         4245.0   
2019-05-03 10:24:00       8.658460     50.123192         4221.0   
2019-05-03 10:20:00       8.658460     50.123192         4221.0   
2019-05-03 10:37:00       8.669688     50.124155         4245.0   

                     End_Station_number  Weekday  Duration  Bikes_on_position  \
End_time                                                                        
2019-05-03 10:23:00              4221.0     True      29.0                  2   
2019-05-03 10:14:00              4245.0     True      21.0                  5   
2019-05-03 10:24:00              4221.0     True      32.0                  5   
2019-05-03 10:20:00              4221.0     True      28.0                  5   
2019-05-03 10:37:00              4188.0     True      24.0                  5   

                     End_Bikes  Zip_codes  count  Month  week  day  hour  
End_time                                                                  
2019-05-03 10:23:00          4      60323      1      5    18    3    10  
2019-05-03 10:14:00          5      60313      1      5    18    3    10  
2019-05-03 10:24:00          5      60323      1      5    18    3    10  
2019-05-03 10:20:00          2      60323      1      5    18    3    10  
2019-05-03 10:37:00          3      60313      1      5    18    3    10

In [86]:
#create a blank map using folium, and add a location marker of the university
ffmap11 = folium.Map(location=[50.107254, 8.685223], zoom_start=10)
folium.Marker(
    [50.130519449999994,8.692339207868319],
    popup=address,
).add_to(ffmap11)

#Using the same method to create heatmap with time
#Create an empty list to store the data
#Then, use the for loop to get the day from the dataframe and use the day to access the data, 
#Then group them by location, and sum the counts for total trips

df_time = []
for day in df_8.day.sort_values().unique():
    df_time.append(df_8.loc[df_8.day == day, ['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist())
    
hm = HeatMapWithTime(df_time, radius=13, min_opacity=0.5, max_opacity=0.8,gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, use_local_extrema=True, auto_play = True)
hm.add_to(ffmap11)
ffmap11

TypeError: __init__() got an unexpected keyword argument 'gradient'

In [ ]:
#Select the month September
#select the time period from 7Am to 8AM for September
#Store in new dataframe
df_9 = df4[df4['Month']==9]
df_9.reset_index(inplace= True)
df_9.set_index('End_time', inplace = True)
df_9 = df_9[df_9['hour'] == 7]
df_9.tail()

In [87]:
#create a blank map using folium, and add a location marker of the university

ffmap11 = folium.Map(location=[50.107254, 8.685223], zoom_start=10)
folium.Marker(
    [50.130519449999994,8.692339207868319],
    popup=address,
).add_to(ffmap11)

#Using the same method to create heatmap with time
#Create an empty list to store the data
#Then, use the for loop to get the day from the dataframe and use the day to access the data, 
#Then group them by location, and sum the counts for total trips

df_time = []
for day in df_9.day.sort_values().unique():
    df_time.append(df_9.loc[df_9.day == day, ['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist())
    
hm = HeatMapWithTime(df_time, radius=13, min_opacity=0.5, max_opacity=0.8,gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, use_local_extrema=True, auto_play = True)
hm.add_to(ffmap11)
ffmap11

NameError: name 'df_9' is not defined

In [88]:
#Select the month October
#select the time period from 7Am to 8AM for October
#Store in new dataframe
df_10 = df4[df4['Month']==10]
df_10.reset_index(inplace= True)
df_10.set_index('End_time', inplace = True)
df_10 = df_10[df_10['hour'] == 7]
df_10.tail()

period_of_day  Unnamed: 0  Bike_number  \
End_time                                                      
2019-10-21 07:38:00  Early Morning      153304        38995   
2019-10-09 07:25:00  Early Morning      154206        38999   
2019-10-22 07:18:00  Early Morning      154227        38999   
2019-10-29 07:29:00  Early Morning      154242        38999   
2019-10-30 07:20:00  Early Morning      154244        38999   

                             Start_Time  Start_Longitude  Start_Latitude  \
End_time                                                                   
2019-10-21 07:38:00 2019-10-21 07:31:00         8.644411       50.116768   
2019-10-09 07:25:00 2019-10-09 06:44:00         8.649362       50.086095   
2019-10-22 07:18:00 2019-10-22 06:59:00         8.664168       50.107599   
2019-10-29 07:29:00 2019-10-29 07:11:00         8.735261       50.106685   
2019-10-30 07:20:00 2019-10-30 07:03:00         8.734413       50.107045   

                     End_Longitude  End_Latitude  Start_Station  \
End_time                                                          
2019-10-21 07:38:00       8.654869     50.112257            0.0   
2019-10-09 07:25:00       8.614503     50.107954         4135.0   
2019-10-22 07:18:00       8.669511     50.108580         4240.0   
2019-10-29 07:29:00       8.714954     50.112489            0.0   
2019-10-30 07:20:00       8.714706     50.112471            0.0   

                     End_Station_number  Weekday  Duration  Bikes_on_position  \
End_time                                                                        
2019-10-21 07:38:00                 0.0     True       7.0                  1   
2019-10-09 07:25:00                 0.0     True      41.0                  4   
2019-10-22 07:18:00              4286.0     True      19.0                 10   
2019-10-29 07:29:00                 0.0     True      18.0                  1   
2019-10-30 07:20:00                 0.0     True      17.0                  1   

                     End_Bikes  Zip_codes  count  Month  week  day  hour  
End_time                                                                  
2019-10-21 07:38:00          1      60486      1     10    43   21     7  
2019-10-09 07:25:00          1      60528      1     10    41    9     7  
2019-10-22 07:18:00          7      60329      1     10    43   22     7  
2019-10-29 07:29:00          1      63067      1     10    44   29     7  
2019-10-30 07:20:00          1      63067      1     10    44   30     7

In [89]:
#create a blank map using folium, and add a location marker of the university
ffmap11 = folium.Map(location=[50.107254, 8.685223], zoom_start=10)
folium.Marker(
    [50.130519449999994,8.692339207868319],
    popup=address,
).add_to(ffmap11)

#Using the same method to create heatmap with time
#Create an empty list to store the data
#Then, use the for loop to get the day from the dataframe and use the day to access the data, 
#Then group them by location, and sum the counts for total trips

df_time = []
for day in df_10.day.sort_values().unique():
    df_time.append(df_10.loc[df_10.day == day, ['End_Latitude', 'End_Longitude', 'count']].groupby(['End_Latitude', 'End_Longitude']).sum().reset_index().values.tolist())
    
hm = HeatMapWithTime(df_time, radius=13, min_opacity=0.5, max_opacity=0.8,gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, use_local_extrema=True, auto_play = True)
hm.add_to(ffmap11)
ffmap11

TypeError: __init__() got an unexpected keyword argument 'gradient'

The heatmaps show that the areas near the University of Applied Sciences were the top popular locations for bike trips to end from 7AM to 8AM in most of the days in May, September, and October. Except for weekends and public holidays, the pattern held true for these three months. In contrast, the heatmap in August shows very few trips ended near the university location from 7AM to 8AM. This could be explained by the fact that August is the summer break time for university students. When the spring semester was ending on August 1st, there were many trips that ended near the university captured. But after that, very few trips ended within the selected time frame.